In [1]:
import pandas as pd
import numpy as np

In [2]:
to_check = pd.read_csv(r'game_recommendations2.csv')
to_check

Title  \
0                         Baldur's Gate 3   
1        Counter-Strike: Global Offensive   
2                           Apex Legends™   
3                         Forza Horizon 5   
4                           Call of Duty®   
...                                   ...   
70332                          Sunkenland   
70333                           The Front   
70334                        The Bornless   
70335                     Winter Memories   
70336  Call of Duty®: Modern Warfare® III   

                                         Recommendations  
0      ['NARAKA: BLADEPOINT', 'Space Engineers', 'Arm...  
1      ['Call of Duty®: Ghosts', 'Team Fortress 2', '...  
2      ['Super Animal Royale', 'Call of Duty®: Modern...  
3      ['Forza Horizon 4', 'Aliens: Fireteam Elite', ...  
4      ['Call of Duty®: Modern Warfare®', 'Call of Du...  
...                                                  ...  
70332  ['ProtoZED', 'Western Rye', 'The Front', 'Tale...  
70333  ['Sunkenland', 'Western Rye', 'ProtoZED', 'POS...  
70334  ['Project Apidom', 'The Slime Plague', 'Angels...  
70335  ['My Furry Girlfriend 🐾', 'Witch World', "Moni...  
70336  ['Battle Of Zodiacs - Card Game', 'Typhon: Bot...  

[70337 rows x 2 columns]

In [3]:
column_names = ['User_ID', 'Game_Name', 'Action', 'Hours', 'To drop']

user_data = pd.read_csv('steam-200k.csv', header=None, names=column_names)
user_data

User_ID                   Game_Name    Action  Hours  To drop
0       151603712  The Elder Scrolls V Skyrim  purchase    1.0        0
1       151603712  The Elder Scrolls V Skyrim      play  273.0        0
2       151603712                   Fallout 4  purchase    1.0        0
3       151603712                   Fallout 4      play   87.0        0
4       151603712                       Spore  purchase    1.0        0
...           ...                         ...       ...    ...      ...
199995  128470551                 Titan Souls      play    1.5        0
199996  128470551  Grand Theft Auto Vice City  purchase    1.0        0
199997  128470551  Grand Theft Auto Vice City      play    1.5        0
199998  128470551                        RUSH  purchase    1.0        0
199999  128470551                        RUSH      play    1.4        0

[200000 rows x 5 columns]

In [4]:
def get_recommendations_by_title(title, dataframe):

    recommendations = dataframe[dataframe['Title'] == title]['Recommendations'].values
    if len(recommendations) > 0:
        return recommendations[0]
    else:
        return f"No recommendations found for game: {title}"
    
game_title = "Sunkenland"
recommended_games = get_recommendations_by_title(game_title, to_check)
print(recommended_games)

['ProtoZED', 'Western Rye', 'The Front', 'Tales of Seikyu', 'Enshrouded', 'Fantasy Craft', 'Shadow Stalker', 'Most Authentic Trench Warfare Simulator', 'SCP: Distorted Spacetime', 'Project Colored Mountains']


In [5]:
user_data = user_data.drop('To drop', axis=1)
user_data.head(5)

User_ID                   Game_Name    Action  Hours
0  151603712  The Elder Scrolls V Skyrim  purchase    1.0
1  151603712  The Elder Scrolls V Skyrim      play  273.0
2  151603712                   Fallout 4  purchase    1.0
3  151603712                   Fallout 4      play   87.0
4  151603712                       Spore  purchase    1.0

In [6]:
import re

def normalize_title(title):

    title = title.lower().strip()
    title = title.replace("®", "")
    title = re.sub(r'[^a-z0-9 ]', '', title)
    return title

to_check['normalized_title'] = to_check['Title'].apply(normalize_title)
user_data['normalized_game_name'] = user_data['Game_Name'].apply(normalize_title)

unique_games_to_check = set(to_check['normalized_title'].unique())

user_data = user_data[user_data['normalized_game_name'].isin(unique_games_to_check)]

to_check.drop('normalized_title', axis=1, inplace=True)
user_data.drop('normalized_game_name', axis=1, inplace=True)

In [7]:
user_data

User_ID          Game_Name    Action  Hours
2       151603712          Fallout 4  purchase    1.0
3       151603712          Fallout 4      play   87.0
4       151603712              Spore  purchase    1.0
5       151603712              Spore      play   14.9
6       151603712  Fallout New Vegas  purchase    1.0
...           ...                ...       ...    ...
199987  128470551       Rogue Legacy      play    2.6
199994  128470551        Titan Souls  purchase    1.0
199995  128470551        Titan Souls      play    1.5
199998  128470551               RUSH  purchase    1.0
199999  128470551               RUSH      play    1.4

[120085 rows x 4 columns]

In [8]:
import ast

def clean_recommendations(recommendation_str):

    if isinstance(recommendation_str, str) and recommendation_str.startswith('[') and recommendation_str.endswith(']'):
        try:
            return ast.literal_eval(recommendation_str)
        except:
            return []
    return []

to_check['Recommendations'] = to_check['Recommendations'].apply(clean_recommendations)

to_check = to_check[to_check['Recommendations'].apply(len) > 0]
to_check

Title  \
0                         Baldur's Gate 3   
1        Counter-Strike: Global Offensive   
2                           Apex Legends™   
3                         Forza Horizon 5   
4                           Call of Duty®   
...                                   ...   
70332                          Sunkenland   
70333                           The Front   
70334                        The Bornless   
70335                     Winter Memories   
70336  Call of Duty®: Modern Warfare® III   

                                         Recommendations  
0      [NARAKA: BLADEPOINT, Space Engineers, Arma 3, ...  
1      [Call of Duty®: Ghosts, Team Fortress 2, Call ...  
2      [Super Animal Royale, Call of Duty®: Modern Wa...  
3      [Forza Horizon 4, Aliens: Fireteam Elite, Ride...  
4      [Call of Duty®: Modern Warfare®, Call of Duty®...  
...                                                  ...  
70332  [ProtoZED, Western Rye, The Front, Tales of Se...  
70333  [Sunkenland, Western Rye, ProtoZED, POSTFROST,...  
70334  [Project Apidom, The Slime Plague, Angels of D...  
70335  [My Furry Girlfriend 🐾, Witch World, Monica's ...  
70336  [Battle Of Zodiacs - Card Game, Typhon: Bot vs...  

[70337 rows x 2 columns]

In [9]:
def get_content_based_recommendations_for_user(user_id, user_data, to_check):
    
    user_played_games = user_data[user_data['User_ID'] == user_id]['Game_Name'].unique()
    
    all_recommendations = []
    
    for game in user_played_games:
        game_recommendations = get_recommendations_by_title(game, to_check)
        all_recommendations.extend(game_recommendations)
    
    unique_recommendations = list(dict.fromkeys(all_recommendations))[:10]
    
    return unique_recommendations

unique_users = user_data['User_ID'].unique()

content_based_results = pd.DataFrame(columns=['User_ID', 'Recommendations'])

for user_id in unique_users:
    recommended_games = get_content_based_recommendations_for_user(user_id, user_data, to_check)
    content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)

content_based_results.to_csv('user_recommendations_ContentBased.csv', index=False)

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

...

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\531835196.py:21: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  content_based_results = content_based_results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C

# Hybrid

In [10]:
def get_recommendations_for_user(user_id, user_data, to_check):

    user_rows = user_data[(user_data['User_ID'] == user_id) & (user_data['Action'] == 'play')]
    user_game_hours = dict(zip(user_rows['Game_Name'], user_rows['Hours']))
    
    recommended_games_weight = {}
    
    for game, hours in user_game_hours.items():

        if game not in to_check['Title'].values:
            continue
        
        recommendations = to_check[to_check['Title'] == game]['Recommendations'].iloc[0]
        
        for recommended_game in recommendations:

            recommended_game = recommended_game.strip()  
            if recommended_game not in recommended_games_weight:
                recommended_games_weight[recommended_game] = hours
            else:
                recommended_games_weight[recommended_game] += hours

    sorted_recommendations = sorted(recommended_games_weight, key=recommended_games_weight.get, reverse=True)

    return sorted_recommendations[:10]


user_id = 151603712  
recommended_games = get_recommendations_for_user(user_id, user_data, to_check)
print(recommended_games)

['Metro Exodus', 'Just Cause™ 3', 'DOOM Eternal', 'DARK SOULS™: REMASTERED', 'Fable Anniversary', "Dragon's Dogma: Dark Arisen", 'DARK SOULS™ III', 'AI＊Shoujo/AI＊少女', 'Senren＊Banka', 'DARK SOULS™ II: Scholar of the First Sin']


In [11]:
results = pd.DataFrame(columns=['User_ID', 'Recommendations'])

unique_users = user_data['User_ID'].unique()

for user_id in unique_users:
    recommended_games = get_recommendations_for_user(user_id, user_data, to_check)
    results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

...

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results = results.append({'User_ID': user_id, 'Recommendations': recommended_games}, ignore_index=True)
C:\Users\user\AppData\Local\Temp\ipykernel_16132\2761002956.py:7: FutureWarning: The 

In [12]:
results.to_csv('user_recommendations.csv', index=False)

In [13]:
user_recommended_data = pd.read_csv('user_recommendations.csv')
user_recommended_data

User_ID                                    Recommendations
0      151603712  ['Metro Exodus', 'Just Cause™ 3', 'DOOM Eterna...
1      187131847  ['The Elder Scrolls V: Skyrim VR', 'Rec Room',...
2       59945701  ['Mafia II (Classic)', 'Sherlock Holmes: Crime...
3       53875128  ['Terraria', 'Call of Duty®: Modern Warfare® 2...
4      140954425  ['Counter-Strike: Global Offensive', 'Call of ...
...          ...                                                ...
10886  125424716  ['Counter-Strike: Global Offensive', 'Call of ...
10887   99096740  ['Dread Hunger', 'The Isle', 'Call of Duty®: M...
10888  176449171  ['Dread Hunger', 'Call of Duty®: Ghosts', 'Cou...
10889  221315846  ['Dread Hunger', 'Call of Duty®: Ghosts', 'Cou...
10890  128470551  ["Conqueror's Blade", 'Crossout', 'Elite Dange...

[10891 rows x 2 columns]

In [14]:
user_recommended_data['Recommendations'] = user_recommended_data['Recommendations'].apply(clean_recommendations)

user_recommended_data = user_recommended_data[user_recommended_data['Recommendations'].apply(len) > 0]
user_recommended_data

User_ID                                    Recommendations
0      151603712  [Metro Exodus, Just Cause™ 3, DOOM Eternal, DA...
1      187131847  [The Elder Scrolls V: Skyrim VR, Rec Room, Dre...
2       59945701  [Mafia II (Classic), Sherlock Holmes: Crimes a...
3       53875128  [Terraria, Call of Duty®: Modern Warfare® 2 (2...
4      140954425  [Counter-Strike: Global Offensive, Call of Dut...
...          ...                                                ...
10886  125424716  [Counter-Strike: Global Offensive, Call of Dut...
10887   99096740  [Dread Hunger, The Isle, Call of Duty®: Modern...
10888  176449171  [Dread Hunger, Call of Duty®: Ghosts, Counter-...
10889  221315846  [Dread Hunger, Call of Duty®: Ghosts, Counter-...
10890  128470551  [Conqueror's Blade, Crossout, Elite Dangerous,...

[8843 rows x 2 columns]